# San Francisco Rental Prices Dashboard

In this notebook, you will compile the visualizations from the previous analysis into functions that can be used for a Panel dashboard.

In [1]:
# initial imports
import os
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
# Initialize the Panel Extensions (for Plotly)
import panel as pn
pn.extension('plotly') # must be loaded before hvplot, in order for pn to be laoded, you have to import panel
import hvplot.pandas
import plotly.express as px
from pathlib import Path
from dotenv import load_dotenv



Bad key "text.kerning_factor" on line 4 in
C:\Users\clear\anaconda3\envs\dev\lib\site-packages\matplotlib\mpl-data\stylelib\_classic_test_patch.mplstyle.
You probably need to get an updated matplotlibrc file from
http://github.com/matplotlib/matplotlib/blob/master/matplotlibrc.template
or from the matplotlib source distribution


# Import Data

In [2]:
# Import the CSVs to Pandas DataFrames
file_path = Path("Data/neighborhoods_census_data.csv")
sfo_data = pd.read_csv(file_path, index_col="year")

file_path = Path("Data/neighborhoods_coordinates.csv")
neighborhood_locations = pd.read_csv(file_path)

- - -

## Panel Visualizations

In this section, you will copy the code for each plot type from your analysis notebook and place it into separate functions that Panel can use to create panes for the dashboard. 

These functions will convert the plot object to a Panel pane.

Be sure to include any DataFrame transformation/manipulation code required along with the plotting code.

Return a Panel pane object from each function that can be used to build the dashboard.

Note: Remove any `.show()` lines from the code. We want to return the plots instead of showing them. The Panel dashboard will then display the plots.

In [3]:
# Define Panel Visualization Functions
def housing_units_per_year():
    """Housing Units Per Year."""
    sfo_data_mean = sfo_data.groupby("year")['housing_units'].mean()
    # YOUR CODE HERE!
    fig_housing_units = sfo_data_mean.hvplot(kind='bar',
    ylim=(sfo_data_mean.min()-sfo_data_mean.std(),sfo_data_mean.max() + sfo_data_mean.std())
).opts(yformatter="%.0f")
    return fig_housing_units

average_gross_rent = sfo_data.groupby("year")["sale_price_sqr_foot", "gross_rent"].mean()
gross_rent=average_gross_rent['gross_rent']
def average_gross_rent():
    """Average Gross Rent in San Francisco Per Year."""


    # YOUR CODE HERE!
    gross_rent_plot = gross_rent.hvplot(kind = "line",
    y=["gross_rent"],
    ylabel= "Gross Rent")
    
    return gross_rent_plot

average_rent = sfo_data.groupby("year")["sale_price_sqr_foot", "gross_rent"].mean()
average_sale = average_rent['sale_price_sqr_foot']
def average_sales_price():
    """Average Sales Price Per Year."""
    
    # YOUR CODE HERE!
    average_sale_plot = average_sale.hvplot(kind="line", 
    y=['sale_price_sqr_foot'],
    ylabel='avg. sale price')
    
    return average_sale_plot

def average_price_by_neighborhood():
    """Average Prices by Neighborhood."""
    average_prices = sfo_data.groupby(["year","neighborhood"]).mean().reset_index().sort_index()
    # YOUR CODE HERE!
    interactive_average = average_prices.hvplot(
        x ='year', 
        y = 'sale_price_sqr_foot', 
        xlabel="year", 
        groupby =['neighborhood'])
    
    return interactive_average

def top_most_expensive_neighborhoods():
    """Top 10 Most Expensive Neighborhoods."""
    neighborhood_mean=sfo_data.groupby('neighborhood').mean().sort_values('sale_price_sqr_foot', ascending=False)
    top_ten = neighborhood_mean[0:10].reset_index()
    # YOUR CODE HERE!
    top_ten_plot = top_ten.hvplot.bar(
                x = "neighborhood", 
                   y="sale_price_sqr_foot", 
                   rot=45,
                   title=(" The Top 10 Most Expensive Neighborhoods"))
    return top_ten_plot

def parallel_coordinates():
    """Parallel Coordinates Plot."""
    neighborhood_mean2=sfo_data.groupby('neighborhood').mean().sort_values('sale_price_sqr_foot', ascending=False)
    top_ten2 = neighborhood_mean2[0:10].reset_index()
    # YOUR CODE HERE!
    top_ten2_plot = px.parallel_coordinates(top_ten2, color='sale_price_sqr_foot')
    
    return top_ten2_plot

def parallel_categories():
    """Parallel Categories Plot."""
    neighborhood_mean3=sfo_data.groupby('neighborhood').mean().sort_values('sale_price_sqr_foot', ascending=False)
    top_ten3 = neighborhood_mean3[0:10].reset_index()
    # YOUR CODE HERE!
    top_ten3_plot = px.parallel_categories(
        top_ten3,
        dimensions=['neighborhood', 'sale_price_sqr_foot','housing_units','gross_rent'],
        color="sale_price_sqr_foot",
        color_continuous_scale=px.colors.sequential.Inferno,)
    
    return top_ten3_plot

In [4]:
load_dotenv()
mapbox_token = os.getenv("MAPBOX_KEY")

In [5]:
px.set_mapbox_access_token(mapbox_token)

In [6]:

# Import the CSVs to Pandas DataFrames
file_path = Path("Data/neighborhoods_census_data.csv")
sfo_data = pd.read_csv(file_path, index_col="year")

file_path = Path("Data/neighborhoods_coordinates.csv")
neighborhood_locations = pd.read_csv(file_path)

In [7]:

def neighborhood_map():
    mean_values = sfo_data.groupby('neighborhood')["sale_price_sqr_foot","housing_units", "gross_rent"].mean().reset_index()
    location_means=pd.concat([neighborhood_locations, mean_values], axis="columns", join="outer")
    fig = px.scatter_mapbox(
                                location_means,
                                hover_name="neighborhood",
                                lat="Lat",
                                lon="Lon",
                                hover_data=["sale_price_sqr_foot"],
                                color="gross_rent",
                                title="Gross Rent & Average Price per Square Foot in San Francisco",
                                )
    fig_pane = pn.pane.Plotly(fig)
   # fig_pane1.updates = True
    return fig_pane


## Panel Dashboard

In this section, you will combine all of the plots into a single dashboard view using Panel. Be creative with your dashboard design!

In [8]:
neighborhood_map_column = pn.Column(
    '## Neighborhood Map', 
    neighborhood_map()
)

neighborhood_prices_column=pn.Column(
    '## Neighborhood Prices Averages', housing_units_per_year(), 
    average_gross_rent(), 
    average_sales_price(),
)

interactive_average_column = pn.Column(
    'Top Ten Most Expensive Neighborhoods', top_most_expensive_neighborhoods(), 
    average_price_by_neighborhood(),
)

parallel_coordinates_column = pn.Column(
    parallel_coordinates(), 
    parallel_categories(),
)

# Create tabs
san_fran_dashboard = pn.Tabs(
    ('San Francisco', neighborhood_map_column),
    ('Neighborhood Averages', neighborhood_prices_column),
    ('Top Ten Most Neighborhoods', interactive_average_column),
    ('Parallal Categories', parallel_coordinates_column)
)


## Serve the Panel Dashboard

In [9]:
san_fran_dashboard.servable()

Tabs
    [0] Column
        [0] Markdown(str)
        [1] Plotly(Figure)
    [1] Column
        [0] Markdown(str)
        [1] HoloViews(Bars)
        [2] HoloViews(Curve)
        [3] HoloViews(Curve)
    [2] Column
        [0] Markdown(str)
        [1] HoloViews(Bars)
        [2] Row
            [0] HoloViews(DynamicMap)
            [1] Column
                [0] WidgetBox
                    [0] Select(margin=(20, 20, 20, 20), name='neighborhood', options=['Alamo Square', ...], value='Alamo Square', width=250)
                [1] VSpacer()
    [3] Column
        [0] Plotly(Figure)
        [1] Plotly(Figure)